## Vectorize <img align="right" src="image/gistda.png" width="200" height="200">
Vectorize is the tools to extract vector(polygon) from raster image.

This tools create polygon by using image segmentation (felzenszwalb).

### Load package

In [1]:
import datacube
from dream_river.convertools import vectorize

### Connect to datacube

In [2]:
dc = datacube.Datacube(app='raster to vector')

### Load dataset

In [3]:
ds = dc.load(product="ls8_collections_sr_scene",
             x=(99.74, 99.84),
             y=(11.75, 11.85),
             measurements = ['red','green','blue', 'nir'],
             time=("2015-01-01","2015-01-31"),
             resolution = (-30, 30),
             output_crs = 'epsg:32647'
            )

ds

<xarray.Dataset>
Dimensions:      (time: 2, y: 371, x: 365)
Coordinates:
  * time         (time) datetime64[ns] 2015-01-04T03:38:36 2015-01-20T03:38:32
  * y            (y) float64 1.31e+06 1.31e+06 1.31e+06 ... 1.299e+06 1.299e+06
  * x            (x) float64 5.806e+05 5.806e+05 ... 5.915e+05 5.915e+05
    spatial_ref  int32 32647
Data variables:
    red          (time, y, x) int16 1377 1312 967 827 762 ... 314 315 315 313
    green        (time, y, x) int16 1105 1073 871 764 706 ... 624 623 619 617
    blue         (time, y, x) int16 739 674 462 391 334 ... 615 608 605 607 611
    nir          (time, y, x) int16 2537 2986 3506 3146 2965 ... 172 179 176 171
Attributes:
    crs:           EPSG:32647
    grid_mapping:  spatial_ref

### Define output name

In [4]:
raster_name= 'training/AOI.tif'
vector_name= 'training/output_satellite.shp'

### Convert raster to polygon using image segmentation (Felzenszwalb)

In [5]:
vectorize(ds, raster_name, vector_name)

 * info: creating integer raster to Polygonize:
   >> training/AOI_int.tif
Success: Wrote training/output_satellite.shp


### Explore output

In [6]:
import geopandas as gpd
gdf = gpd.read_file(vector_name)
gdf.head()

values                                           geometry
0       3  POLYGON ((589290.000 1310130.000, 589320.000 1...
1      61  POLYGON ((588210.000 1310100.000, 588240.000 1...
2       3  POLYGON ((589320.000 1310100.000, 589350.000 1...
3      75  POLYGON ((590280.000 1310100.000, 590310.000 1...
4       3  POLYGON ((589350.000 1310070.000, 589380.000 1...

In [7]:
gdf.crs

<Derived Projected CRS: EPSG:32647>
Name: WGS 84 / UTM zone 47N
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- name: Between 96°E and 102°E, northern hemisphere between equator and 84°N, onshore and offshore. China. Indonesia. Laos. Malaysia - West Malaysia. Mongolia. Myanmar (Burma). Russian Federation. Thailand.
- bounds: (96.0, 0.0, 102.0, 84.0)
Coordinate Operation:
- name: UTM zone 47N
- method: Transverse Mercator
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [8]:
gdf.explore()

### Convert Shp to Geojson and define CRS 4326

In [9]:
from dream_river.geobox import convert_geojson_CRS

path='training/output_satellite.shp'
outpath='training/output_satellite4326.geojson'

convert_geojson_CRS(path, outpath, crs=4326)

### Explore output

In [10]:
from dream_river.plotimg import show_vector

filepath=['training/output_satellite4326.geojson']

show_vector(filepath)